### The Battle of Neighborhoods (Week 2)

<h5> A description of the problem and a discussion of the background </h5>

Bengaluru (old name Bangalore) is IT hub of India. College grads migrate from different states to start their IT career in Bengaluru. 50% population of this city is migrant. Bengaluru comes in top 10 Indian cities for multilingual people. Because of massive development of IT industry in this city, there are other industries and businesses growing here like real state, hotel/hospitality industry, restaurants,e-Commerce and retail industry. Because of the diversity, different type of people like to spend their weekends and holidays differently, some people like visit restaurants and bars,some people like to spend time with family and kids in shopping malls and some people like to go for trips. If someone is looking to open a new business, a restaurant or superstore, s/he would need to understand population density of different neighborhoods of Bengaluru and already existing restaurants, bars and superstores.

<h5>A description of the data and how it will be used to solve the problem</h5>

I would collect population density of different neighborhood of Bengaluru. Using latitude and longitude for the neighborhood, I would explore them for restaurants/bars/superstore/malls with the help of Foursquare APIs.  
Higher population density with less number of restaurants/bars/superstore/malls would be the best places to start a new business.

<h5>Data Source</h5>

Bruhat Bengaluru Mahanagara Palike (BBMP) official website

http://bbmp.gov.in/documents/10180/460906/BBMPR_ward_master_BBMP+Restructuring+03-08-2015.pdf

Importing libraries to use in my analysis

In [174]:
import pandas as pd
import requests 
import folium # map rendering library
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

Importing data from local excel file

In [4]:
df_data=pd.read_excel(r'C:\Users\sanjay_godiya\Desktop\MyDocs\DataScience\Lab_data\BBMP_Ward_Master_2011.xlsx',
                      sheet_name='Sheet1')

In [5]:
df_data.head(10)

Ward_Name  Population_density_(persons_per_sq_km)
0           Kempegowda Ward                                    3182
1          Chowdeswari Ward                                    5635
2                    Atturu                                    6606
3  Yelahanka Satellite Town                                    9224
4                   Jakkuru                                    2215
5               Thanisandra                                    7161
6           Byatarayanapura                                    7198
7               Kodigehalli                                   12369
8            Vidyaranyapura                                    5753
9         Dodda Bommasandra                                    8673

In [6]:
df_data.shape

(198, 2)

Defining a function to find latitude and longitude values of different neighbourhoods of Bangalore

In [8]:
def getBlrData(ward_name,population_density):
    data=[]
    for name,density in zip (ward_name,population_density):
        row=[]
        address = name +', Bangalore, India'
        geolocator = Nominatim(user_agent="ny_explorer")
        location = geolocator.geocode(address)
        if location is not None:
            lat = location.latitude
            long = location.longitude
            row.append(name)
            row.append(density)
            row.append(lat)
            row.append(long)
        data.append(row)
    return(data)

In [9]:
df_data['Ward_Name']=df_data['Ward_Name'].str.replace('Ward','')
df_data.columns=df_data.columns.str.strip()
blr_data=getBlrData(ward_name=df_data['Ward_Name'],
                    population_density=df_data['Population_density_(persons_per_sq_km)'])

In [10]:
Bangalore_df=pd.DataFrame(blr_data,columns=['Neighbourhood','Population_density_(persons_per_sq_km)','Latitude','Longitude'])
Bangalore_df.dropna(how='any',inplace=True)
Bangalore_df['Population_density_(persons_per_sq_km)']=Bangalore_df['Population_density_(persons_per_sq_km)'].astype(int)
Bangalore_df.head()

Neighbourhood  Population_density_(persons_per_sq_km)  \
0               Kempegowda                                     3182   
1              Chowdeswari                                     5635   
2                    Atturu                                    6606   
3  Yelahanka Satellite Town                                    9224   
4                   Jakkuru                                    2215   

    Latitude  Longitude  
0  13.109018  77.601900  
1  13.120459  77.579618  
2  13.100409  77.858725  
3  13.089139  77.582717  
4  13.098320  77.625146

In [11]:
Bangalore_df.shape

(168, 4)

In [12]:
address = 'Bangalore, India'
geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
blr_lat = location.latitude
blr_long = location.longitude
print('The geograpical coordinates of Bangalore are {}, {}.'.format(blr_lat, blr_long))

The geograpical coordinates of Bangalore are 12.9791198, 77.5912997.


Plotting different neighbourhoods of Bangalore using Folium

In [13]:
map_blr = folium.Map(location=[blr_lat, blr_long], zoom_start=10)
# add markers to map
for lat, lng, label,density in zip(Bangalore_df['Latitude'], Bangalore_df['Longitude'], Bangalore_df['Neighbourhood'],
                           Bangalore_df['Population_density_(persons_per_sq_km)']):
    label = folium.Popup(label+','+ str(density), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='yellow',
        fill_opacity=0.7,
        parse_html=False).add_to(map_blr) 
map_blr

Defining Foursquare Credentials and Version<br>
I will utilize the Foursquare API to explore the neighborhoods and segment them.

In [148]:
CLIENT_ID = 'EWWJ54CJ55IE1TC0SLXR10STUZK3NY0MCIHU3HU0ABVIIDYA' #Foursquare ID
CLIENT_SECRET = 'XDMSRVNYZJNRT15V2XWSWCAG5FKFNJSP5UPNEDXDV33U2X23' #Foursquare Secret
VERSION = '20200101' # Foursquare API version

Creating a function to explore 500 venues at each neighbourhood

In [149]:
LIMIT=500
def getNearbyVenues(names,densities,latitudes,longitudes):   
    venues_list=[]
    for name,dens,lat,lng in zip(names,densities,latitudes,longitudes):
            
        # API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&limit={}'.format(
            CLIENT_ID,CLIENT_SECRET,VERSION,lat,lng,LIMIT)
            
        # GET request
        results = requests.get(url).json()['response']['groups'][0]['items']
        #print(results)
        
        # append only relevant information for each nearby venue
        venues_list.append([(name,dens,lat,lng,v['venue']['name'],v['venue']['location']['lat'],v['venue']['location']['lng'],
                             v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood','Population_density_(persons_per_sq_km)','Latitude','Longitude',
                             'Venue','Venue_Latitude','Venue_Longitude', 'Venue_Category']
    
    return(nearby_venues)

In [150]:
blr_venues = getNearbyVenues(names=Bangalore_df['Neighbourhood'],densities=Bangalore_df['Population_density_(persons_per_sq_km)'],
                             latitudes=Bangalore_df['Latitude'],longitudes=Bangalore_df['Longitude'])
blr_venues

Neighbourhood  Population_density_(persons_per_sq_km)   Latitude  \
0       Kempegowda                                     3182  13.109018   
1       Kempegowda                                     3182  13.109018   
2       Kempegowda                                     3182  13.109018   
3       Kempegowda                                     3182  13.109018   
4       Kempegowda                                     3182  13.109018   
5       Kempegowda                                     3182  13.109018   
6       Kempegowda                                     3182  13.109018   
7       Kempegowda                                     3182  13.109018   
8       Kempegowda                                     3182  13.109018   
9       Kempegowda                                     3182  13.109018   
10      Kempegowda                                     3182  13.109018   
11      Kempegowda                                     3182  13.109018   
12      Kempegowda                                     3182  13.109018   
13      Kempegowda                                     3182  13.109018   
14      Kempegowda                                     3182  13.109018   
15      Kempegowda                                     3182  13.109018   
16      Kempegowda                                     3182  13.109018   
17      Kempegowda                                     3182  13.109018   
18      Kempegowda                                     3182  13.109018   
19      Kempegowda                                     3182  13.109018   
20      Kempegowda                                     3182  13.109018   
21      Kempegowda                                     3182  13.109018   
22      Kempegowda                                     3182  13.109018   
23      Kempegowda                                     3182  13.109018   
24      Kempegowda                                     3182  13.109018   
25      Kempegowda                                     3182  13.109018   
26      Kempegowda                                     3182  13.109018   
27      Kempegowda                                     3182  13.109018   
28      Kempegowda                                     3182  13.109018   
29      Kempegowda                                     3182  13.109018   
...             ...                                     ...        ...   
12367   Hemmigepura                                    1652  12.881929   
12368   Hemmigepura                                    1652  12.881929   
12369   Hemmigepura                                    1652  12.881929   
12370   Hemmigepura                                    1652  12.881929   
12371   Hemmigepura                                    1652  12.881929   
12372   Hemmigepura                                    1652  12.881929   
12373   Hemmigepura                                    1652  12.881929   
12374   Hemmigepura                                    1652  12.881929   
12375   Hemmigepura                                    1652  12.881929   
12376   Hemmigepura                                    1652  12.881929   
12377   Hemmigepura                                    1652  12.881929   
12378   Hemmigepura                                    1652  12.881929   
12379   Hemmigepura                                    1652  12.881929   
12380   Hemmigepura                                    1652  12.881929   
12381   Hemmigepura                                    1652  12.881929   
12382   Hemmigepura                                    1652  12.881929   
12383   Hemmigepura                                    1652  12.881929   
12384   Hemmigepura                                    1652  12.881929   
12385   Hemmigepura                                    1652  12.881929   
12386   Hemmigepura                                    1652  12.881929   
12387   Hemmigepura                                    1652  12.881929   
12388   Hemmigepura                                    1652  12.881929   
12389   He

Category wise venue count

In [152]:
blr_venues['Venue_Category'].value_counts()

Indian Restaurant                  1995
Café                                877
Fast Food Restaurant                615
Ice Cream Shop                      601
Pizza Place                         510
Coffee Shop                         449
Hotel                               290
Bakery                              286
Chinese Restaurant                  277
Italian Restaurant                  234
Vegetarian / Vegan Restaurant       210
Restaurant                          203
Lounge                              199
Breakfast Spot                      198
Sandwich Place                      193
Department Store                    189
Multiplex                           175
Clothing Store                      159
Snack Place                         157
Shopping Mall                       147
Brewery                             144
Donut Shop                          131
Asian Restaurant                    131
Seafood Restaurant                  127
Park                                125


Filtering dataset for all types of restaurants

In [178]:
blr_restaurants=blr_venues[blr_venues['Venue_Category'].str.contains('Restaurant')]
blr_restaurants_grouped=blr_restaurants.groupby(['Neighbourhood','Venue_Category','Population_density_(persons_per_sq_km)'])[['Venue_Category']].count()

In [179]:
blr_restaurants_grouped=blr_restaurants_grouped.add_suffix('_Count').reset_index()

In [180]:
blr_restaurants_grouped.sort_values(by=['Population_density_(persons_per_sq_km)'],ascending=False)

Neighbourhood                   Venue_Category  \
1154      Padarayanapura             Fast Food Restaurant   
1155      Padarayanapura                Indian Restaurant   
1156      Padarayanapura                       Restaurant   
1157      Padarayanapura               Seafood Restaurant   
1153      Padarayanapura                 Asian Restaurant   
856   Kempapura Agrahara    Vegetarian / Vegan Restaurant   
855   Kempapura Agrahara             Karnataka Restaurant   
854   Kempapura Agrahara                Indian Restaurant   
853   Kempapura Agrahara             Himalayan Restaurant   
1141          Nilasandra        Middle Eastern Restaurant   
1142          Nilasandra  Southern / Soul Food Restaurant   
1131          Nilasandra                Andhra Restaurant   
1140          Nilasandra         Mediterranean Restaurant   
1132          Nilasandra                 Asian Restaurant   
1133          Nilasandra               Chinese Restaurant   
1134          Nilasandra             Fast Food Restaurant   
1135          Nilasandra                Indian Restaurant   
1136          Nilasandra               Italian Restaurant   
1137          Nilasandra             Karnataka Restaurant   
1138          Nilasandra                Kerala Restaurant   
1139          Nilasandra                Korean Restaurant   
1369       Shivaji Nagar                Indian Restaurant   
1366       Shivaji Nagar      Eastern European Restaurant   
1367       Shivaji Nagar             Fast Food Restaurant   
1368       Shivaji Nagar            Hyderabadi Restaurant   
1373       Shivaji Nagar          South Indian Restaurant   
1370       Shivaji Nagar               Italian Restaurant   
1371       Shivaji Nagar        Middle Eastern Restaurant   
1372       Shivaji Nagar               Seafood Restaurant   
1363       Shivaji Nagar              American Restaurant   
...                  ...                              ...   
184           Bellanduru               Italian Restaurant   
183           Bellanduru                Indian Restaurant   
178           Bellanduru                Andhra Restaurant   
182           Bellanduru             Fast Food Restaurant   
641              Jakkuru    Vegetarian / Vegan Restaurant   
639              Jakkuru               Mexican Restaurant   
638              Jakkuru               Italian Restaurant   
637              Jakkuru                Indian Restaurant   
636              Jakkuru             Fast Food Restaurant   
635              Jakkuru              American Restaurant   
640              Jakkuru          South Indian Restaurant   
1499             Varthur                       Restaurant   
1491             Varthur               Chinese Restaurant   
1500             Varthur    Vegetarian / Vegan Restaurant   
1497             Varthur         Maharashtrian Restaurant   
1498             Varthur            Rajasthani Restaurant   
1492             Varthur      Eastern European Restaurant   
1496             Varthur                Kerala Restaurant   
1495             Varthur               Italian Restaurant   
1494             Varthur                Indian Restaurant   
1493             Varthur             Fast Food Restaurant   
1489             Varthur              American Restaurant   
1490             Varthur                Andhra Restaurant   
536          Hemmigepura               Chinese Restaurant   
537          Hemmigepura             Fast Food Restaurant   
538          Hemmigepura        Indian Chinese Restaurant   
539          Hemmigepura                Indian Restaurant   
540          Hemmigepura                       Restaurant   
541          Hemmigepura          South Indian Restaurant   
542          Hemmigepura    Vegetarian / Vegan Restaurant   

      Population_density_(persons_per_sq_km)  Venue_Category_Count  
1154                                  118059                     6  
1155                                  118059                    17  
1156                 

Plotting all restaurants of Bangalore


In [156]:
map_blr_venues = folium.Map(location=[blr_lat, blr_long], zoom_start=10)
# add markers to map
for lat, lng, label,neigh in zip(blr_restaurants['Venue_Latitude'], blr_restaurants['Venue_Longitude'], 
                                 blr_restaurants['Venue_Category'],
                                 blr_restaurants['Neighbourhood']):
    label = folium.Popup(label+','+neigh, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='yellow',
        fill_opacity=0.7,
        parse_html=False).add_to(map_blr_venues) 
map_blr_venues

## Results

Finding top 10 most dens areas of Bangalore

In [157]:
top10_dens=Bangalore_df.sort_values(by='Population_density_(persons_per_sq_km)',ascending=False).head(10)
top10_dens

Neighbourhood  Population_density_(persons_per_sq_km)   Latitude  \
134      Padarayanapura                                  118059  12.963801   
121  Kempapura Agrahara                                  113291  13.154848   
115          Nilasandra                                   94287  12.951245   
91        Shivaji Nagar                                   87856  12.989158   
136           Rayapuram                                   81770  12.964870   
96      Dayananda Nagar                                   80035  12.991025   
47     Muneshwara Nagar                                   74511  13.014081   
133        Bapuji Nagar                                   72549  12.954321   
170     Gurappana Palya                                   72068  12.920758   
29     Kadugondanahalli                                   65514  13.015587   

     Longitude  
134  77.547523  
121  77.289579  
115  77.614791  
91   77.606089  
136  77.556562  
96   77.564519  
47   77.611474  
133  77.539697  
170  77.603333  
29   77.620031

Finding restaurants for top 10 most dens areas of Bangalore

In [159]:
blr_restaurants_grouped[blr_restaurants_grouped.Neighbourhood.isin(top10_dens['Neighbourhood'].tolist())].sort_values(by='Population_density_(persons_per_sq_km)',ascending=False)

Neighbourhood                   Venue_Category  \
1153      Padarayanapura                 Asian Restaurant   
1154      Padarayanapura             Fast Food Restaurant   
1155      Padarayanapura                Indian Restaurant   
1156      Padarayanapura                       Restaurant   
1157      Padarayanapura               Seafood Restaurant   
854   Kempapura Agrahara                Indian Restaurant   
853   Kempapura Agrahara             Himalayan Restaurant   
856   Kempapura Agrahara    Vegetarian / Vegan Restaurant   
855   Kempapura Agrahara             Karnataka Restaurant   
1138          Nilasandra                Kerala Restaurant   
1139          Nilasandra                Korean Restaurant   
1140          Nilasandra         Mediterranean Restaurant   
1142          Nilasandra  Southern / Soul Food Restaurant   
1141          Nilasandra        Middle Eastern Restaurant   
1136          Nilasandra               Italian Restaurant   
1135          Nilasandra                Indian Restaurant   
1134          Nilasandra             Fast Food Restaurant   
1133          Nilasandra               Chinese Restaurant   
1132          Nilasandra                 Asian Restaurant   
1131          Nilasandra                Andhra Restaurant   
1137          Nilasandra             Karnataka Restaurant   
1362       Shivaji Nagar                Afghan Restaurant   
1374       Shivaji Nagar    Vegetarian / Vegan Restaurant   
1363       Shivaji Nagar              American Restaurant   
1364       Shivaji Nagar                 Asian Restaurant   
1365       Shivaji Nagar               Chinese Restaurant   
1366       Shivaji Nagar      Eastern European Restaurant   
1367       Shivaji Nagar             Fast Food Restaurant   
1369       Shivaji Nagar                Indian Restaurant   
1370       Shivaji Nagar               Italian Restaurant   
...                  ...                              ...   
135         Bapuji Nagar             Fast Food Restaurant   
136         Bapuji Nagar                Indian Restaurant   
137         Bapuji Nagar               Seafood Restaurant   
138         Bapuji Nagar              Szechuan Restaurant   
133         Bapuji Nagar                Andhra Restaurant   
134         Bapuji Nagar                 Asian Restaurant   
450      Gurappana Palya            Rajasthani Restaurant   
448      Gurappana Palya               Italian Restaurant   
443      Gurappana Palya                 Asian Restaurant   
444      Gurappana Palya               Chinese Restaurant   
445      Gurappana Palya               Dim Sum Restaurant   
446      Gurappana Palya             Fast Food Restaurant   
452      Gurappana Palya    Vegetarian / Vegan Restaurant   
451      Gurappana Palya                       Restaurant   
447      Gurappana Palya                Indian Restaurant   
449      Gurappana Palya        Middle Eastern Restaurant   
799     Kadugondanahalli               Seafood Restaurant   
798     Kadugondanahalli                       Restaurant   
797     Kadugondanahalli             Pakistani Restaurant   
795     Kadugondanahalli         Mediterranean Restaurant   
794     Kadugondanahalli                Korean Restaurant   
786     Kadugondanahalli               Chinese Restaurant   
787     Kadugondanahalli               Falafel Restaurant   
788     Kadugondanahalli             Fast Food Restaurant   
796     Kadugondanahalli        Middle Eastern Restaurant   
790     Kadugondanahalli        Indian Chinese Restaurant   
791     Kadugondanahalli                Indian Restaurant   
792     Kadugondanahalli               Italian Restaurant   
793     Kadugondanahalli                Kerala Restaurant   
789     Kadugondanahalli            Hyderabadi Restaurant   

      Population_density_(persons_per_sq_km)  Venue_Category_Count  
1153                                  118059                     2  
1154                                  118059                     6  
1155                 

Finding top 10 least dens areas of Bangalore

In [158]:
least10_dens=Bangalore_df.sort_values(by='Population_density_(persons_per_sq_km)',ascending=True).head(10)
least10_dens

Neighbourhood  Population_density_(persons_per_sq_km)   Latitude  \
197   Hemmigepura                                    1652  12.881929   
148       Varthur                                    1929  12.940615   
4         Jakkuru                                    2215  13.098320   
149    Bellanduru                                    3041  12.929211   
0     Kempegowda                                     3182  13.109018   
113        Agaram                                    3345  12.945704   
53           Hudi                                    3349  13.058506   
82       Kadugodi                                    3934  12.998577   
195    Anjanapura                                    3997  12.858081   
83        Hagadur                                    4003  12.963344   

     Longitude  
197  77.485497  
148  77.746994  
4    77.625146  
149  77.677042  
0    77.601900  
113  77.637886  
53   77.671339  
82   77.760972  
195  77.558071  
83   77.747285

Finding restaurants for top 10 least dens areas of Bangalore

In [160]:
blr_restaurants_grouped[blr_restaurants_grouped.Neighbourhood.isin(least10_dens['Neighbourhood'].tolist())].sort_values(by='Population_density_(persons_per_sq_km)',ascending=True)

Neighbourhood                 Venue_Category  \
539    Hemmigepura              Indian Restaurant   
538    Hemmigepura      Indian Chinese Restaurant   
540    Hemmigepura                     Restaurant   
541    Hemmigepura        South Indian Restaurant   
542    Hemmigepura  Vegetarian / Vegan Restaurant   
537    Hemmigepura           Fast Food Restaurant   
536    Hemmigepura             Chinese Restaurant   
1492       Varthur    Eastern European Restaurant   
1494       Varthur              Indian Restaurant   
1490       Varthur              Andhra Restaurant   
1489       Varthur            American Restaurant   
1495       Varthur             Italian Restaurant   
1496       Varthur              Kerala Restaurant   
1497       Varthur       Maharashtrian Restaurant   
1499       Varthur                     Restaurant   
1498       Varthur          Rajasthani Restaurant   
1493       Varthur           Fast Food Restaurant   
1491       Varthur             Chinese Restaurant   
1500       Varthur  Vegetarian / Vegan Restaurant   
641        Jakkuru  Vegetarian / Vegan Restaurant   
635        Jakkuru            American Restaurant   
636        Jakkuru           Fast Food Restaurant   
639        Jakkuru             Mexican Restaurant   
638        Jakkuru             Italian Restaurant   
637        Jakkuru              Indian Restaurant   
640        Jakkuru        South Indian Restaurant   
189     Bellanduru  Vegetarian / Vegan Restaurant   
188     Bellanduru             Seafood Restaurant   
186     Bellanduru        North Indian Restaurant   
185     Bellanduru              Kerala Restaurant   
...            ...                            ...   
775       Kadugodi             Chinese Restaurant   
782       Kadugodi             Mexican Restaurant   
773       Kadugodi            American Restaurant   
781       Kadugodi       Maharashtrian Restaurant   
784       Kadugodi                     Restaurant   
785       Kadugodi  Vegetarian / Vegan Restaurant   
774       Kadugodi               Asian Restaurant   
783       Kadugodi          Rajasthani Restaurant   
50      Anjanapura  Vegetarian / Vegan Restaurant   
49      Anjanapura        South Indian Restaurant   
47      Anjanapura          Rajasthani Restaurant   
45      Anjanapura              Indian Restaurant   
42      Anjanapura            American Restaurant   
43      Anjanapura             Chinese Restaurant   
46      Anjanapura             Italian Restaurant   
48      Anjanapura                     Restaurant   
44      Anjanapura           Fast Food Restaurant   
512        Hagadur             Mexican Restaurant   
511        Hagadur       Maharashtrian Restaurant   
510        Hagadur              Kerala Restaurant   
509        Hagadur             Italian Restaurant   
514        Hagadur                     Restaurant   
507        Hagadur           Fast Food Restaurant   
506        Hagadur             Falafel Restaurant   
505        Hagadur    Eastern European Restaurant   
504        Hagadur             Chinese Restaurant   
503        Hagadur            American Restaurant   
515        Hagadur  Vegetarian / Vegan Restaurant   
513        Hagadur          Rajasthani Restaurant   
508        Hagadur              Indian Restaurant   

      Population_density_(persons_per_sq_km)  Venue_Category_Count  
539                                     1652                     6  
538                                     1652                     1  
540                                     1652                     3  
541                                     1652                     1  
542                                     1652                     1  
537                                     1652                     1  
536                                     1652                     1  
1492                                    1929                     2  
1494                                    1929                    12  
1490                        

###### Plotting Restaurants for top 10 most dens areas of Bangalore

In [162]:
blr_restaurants_top10=blr_restaurants[blr_restaurants.Neighbourhood.isin(top10_dens['Neighbourhood'].tolist())]

In [167]:
map_blr_restaurants_top10 = folium.Map(location=[blr_lat, blr_long], zoom_start=10)
# add markers to map
for lat, lng, label,neigh in zip(blr_restaurants_top10['Venue_Latitude'], blr_restaurants_top10['Venue_Longitude'], 
                                 blr_restaurants_top10['Venue_Category'],
                                 blr_restaurants_top10['Neighbourhood']):
    label = folium.Popup(label+','+neigh, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='yellow',
        fill_opacity=0.7,
        parse_html=False).add_to(map_blr_restaurants_top10) 
map_blr_restaurants_top10

###### Plotting Restaurants for top 10 least dens areas of Bangalore

In [168]:
blr_restaurants_least10=blr_restaurants[blr_restaurants.Neighbourhood.isin(least10_dens['Neighbourhood'].tolist())]

In [169]:
map_blr_restaurants_least10= folium.Map(location=[blr_lat, blr_long], zoom_start=10)
# add markers to map
for lat, lng, label,neigh in zip(blr_restaurants_least10['Venue_Latitude'], blr_restaurants_least10['Venue_Longitude'], 
                                 blr_restaurants_least10['Venue_Category'],
                                 blr_restaurants_least10['Neighbourhood']):
    label = folium.Popup(label+','+neigh, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='yellow',
        fill_opacity=0.7,
        parse_html=False).add_to(map_blr_restaurants_least10) 
map_blr_restaurants_least10

Finding neighbourhoods having no venues of any category. <br>
These neighbourhoods could be potential locations to start a new business. 

In [161]:
Bangalore_df[~Bangalore_df.Neighbourhood.isin(blr_restaurants_grouped['Neighbourhood'].tolist())].sort_values(by='Population_density_(persons_per_sq_km)',ascending=True)

Neighbourhood  Population_density_(persons_per_sq_km)   Latitude  Longitude
38  Chokkasandra                                   15752  13.187971  77.901090
33  Gangenahalli                                   22226  12.983417  77.391874

Total restaurants count for top 10 least dens neighbourhoods of Bangalore

In [189]:
blr_restaurants_grouped[blr_restaurants_grouped.Neighbourhood.isin(least10_dens['Neighbourhood'].tolist())].groupby(['Neighbourhood','Population_density_(persons_per_sq_km)'])['Venue_Category_Count'].sum()

Neighbourhood  Population_density_(persons_per_sq_km)
Agaram         3345                                      31
Anjanapura     3997                                      16
Bellanduru     3041                                      25
Hagadur        4003                                      32
Hemmigepura    1652                                      14
Hudi           3349                                      26
Jakkuru        2215                                      19
Kadugodi       3934                                      35
Kempegowda     3182                                      15
Varthur        1929                                      41
Name: Venue_Category_Count, dtype: int64

Total restaurants count for top 10 most dens neighbourhoods of Bangalore

In [190]:
blr_restaurants_grouped[blr_restaurants_grouped.Neighbourhood.isin(top10_dens['Neighbourhood'].tolist())].groupby(['Neighbourhood','Population_density_(persons_per_sq_km)'])['Venue_Category_Count'].sum()

Neighbourhood       Population_density_(persons_per_sq_km)
Bapuji Nagar        72549                                     23
Dayananda Nagar     80035                                     39
Gurappana Palya     72068                                     48
Kadugondanahalli    65514                                     47
Kempapura Agrahara  113291                                     5
Muneshwara Nagar    74511                                     43
Nilasandra          94287                                     25
Padarayanapura      118059                                    27
Rayapuram           81770                                     29
Shivaji Nagar       87856                                     38
Name: Venue_Category_Count, dtype: int64

## Observation

The number of restaurants in top 10 least dens areas are very high compare to number of restaurants in top 10 most dens areas.
It means there are opportunities to open new restaurants in dens areas.


Kempapura Agrahara having population density of 113291 person/sq-km has only 5 restaurants which is very less compare to its nearby neighbourhood Padarayanapura (population density 118059 person/sq-km) which has 27 restaurants. Kempapura Agrahara can also be a good location to start a new restaurant business.

Chokkasandra and Gangenahalli neighbourhoods has no single venue of any category so these locations are good to start restaurants, fast-food centers or super stores.